# Motor selection
*Written by Marc Budinger (INSA Toulouse), Scott Delbecq (ISAE-SUPAERO) and Félix Pollet (ISAE-SUPAERO), Toulouse, France.*

## Design graph 

The following diagram represents the design graph of the motor’s selection. The mean speed/thrust (Ωmoy & Tmoy), the max speed/thrust (Ωmax & Tmax) and the battery voltage are assumed to be known here.



```{figure} ./assets/design_graphs/DesignGraphs_motor.svg
:name: design_graph_motor
:align: center
:width: 50%

Motor design graph
```

The design graphs for the overall drone system can be found in [here](./assets/design_graphs/DesignGraphs_Overall_Solution.pdf).


### Sizing code


In [6]:
# Specifications

# Reference parameters for scaling laws
# Motor reference
# Ref : AXI 5325/16 GOLD LINE
T_nom_mot_ref = 2.32  # [N.m] rated torque
T_max_mot_ref = 85.0 / 70.0 * T_nom_mot_ref  # [N.m] max torque
R_mot_ref = 0.03  # [Ohm] resistance
M_mot_ref = 0.575  # [kg] mass
K_T_ref = 0.03  # [N.m/A] torque coefficient
T_mot_fr_ref = 0.03  # [N.m] friction torque (zero load, nominal speed)

# Assumptions
T_pro_to = 0.5  # [N.m] Propeller Torque during takeoff
P_pro_to = 100  # [W] Propeller Power during takeoff
Omega_pro_to = 400.0  # [rad/s] Propeller speed during takeoff
T_pro_hov = 1.0  # [N.m] Propeller Torque during hover
P_pro_hov = 50  # [W] Propeller Power during hover
Omega_pro_hov = 0.22  # [rad/s] Propeller speed during hover
U_bat_est = 14.0  # [V] Battery voltage value (estimation)

# Design variables
k_vb = 1.0  # oversizing coefficient for voltage evaluation
k_mot = 1.0  # over sizing coefficient on the motor torque
k_speed_mot = 1.2  # adaption winding coef on the motor speed

In [7]:
# Equations

# Nominal torque selection with hover scenario
T_nom_mot = k_mot * T_pro_hov  # [N*m] Motor nominal torque per propeller

# Torque constant selection with take-off scenario
U_bat = k_vb * 1.84 * P_pro_to ** (0.36)  # [V] battery voltage estimation
K_T = U_bat / (k_speed_mot * Omega_pro_to)  # [N*m/A] or [V/(rad/s)] Kt motor

# Estimation models
M_mot = M_mot_ref * (T_nom_mot / T_nom_mot_ref) ** (3.0 / 3.5)  # [kg] Motor mass
R_mot = (
    R_mot_ref * (T_nom_mot / T_nom_mot_ref) ** (-5.0 / 3.5) * (K_T / K_T_ref) ** 2.0
)  # [ohm] motor resistance
T_mot_fr = T_mot_fr_ref * (T_nom_mot / T_nom_mot_ref) ** (3.0 / 3.5)  # [N*m] Friction torque
T_max_mot = T_max_mot_ref * (T_nom_mot / T_nom_mot_ref)  # [N*m] Max. torque

# Performance in various operating conditions
# Hover current and voltage
I_mot_hov = (T_pro_hov + T_mot_fr) / K_T  # [A] Current of the motor per propeller
U_mot_hov = R_mot * I_mot_hov + Omega_pro_hov * K_T  # [V] Voltage of the motor per propeller
P_el_mot_hov = U_mot_hov * I_mot_hov  # [W] Hover : electrical power
# Takeoff current and voltage
I_mot_to = (T_pro_to + T_mot_fr) / K_T  # [A] Current of the motor per propeller
U_mot_to = R_mot * I_mot_to + Omega_pro_to * K_T  # [V] Voltage of the motor per propeller
P_el_mot_to = U_mot_to * I_mot_to  # [W] Takeoff : electrical power

In [8]:
%whos

Variable        Type     Data/Info
----------------------------------
I_mot_hov       float    50.43255613781267
I_mot_to        float    25.57872068611814
K_T             float    0.020117619309574616
K_T_ref         float    0.03
M_mot           float    0.279506832794264
M_mot_ref       float    0.575
Omega_pro_hov   float    0.22
Omega_pro_to    float    400.0
P_el_mot_hov    float    114.400456104866
P_el_mot_to     float    235.20395039293444
P_pro_hov       int      50
P_pro_to        int      100
R_mot           float    0.04489082730970943
R_mot_ref       float    0.03
T_max_mot       float    1.2142857142857142
T_max_mot_ref   float    2.8171428571428567
T_mot_fr        float    0.014582965189265948
T_mot_fr_ref    float    0.03
T_nom_mot       float    1.0
T_nom_mot_ref   float    2.32
T_pro_hov       float    1.0
T_pro_to        float    0.5
U_bat           float    9.656457268595815
U_bat_est       float    14.0
U_mot_hov       float    2.2683850446178813
U_mot_to        f